In [ ]:
import requests
import json
import requests
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.colors import Normalize
from matplotlib.animation import FFMpegWriter
H = np.loadtxt('topography_180x360_grid.txt')
def get_coordinates(x, y):
    lon = (x / 359) * 360 - 180
    lat = 90 - (y / 179) * 180
    return (lat, lon)
coordinates = []
for y in range(H.shape[0]):
    for x in range(H.shape[1]):
        coordinates.append(get_coordinates(x,y))

In [ ]:
# import requests
# import json
# import requests
# H = np.loadtxt('topography_180x360_grid.txt')
# all_responses = []
# for lat,lon in coordinates:
#     response = requests.get(f'http://api.weatherapi.com/v1/current.json?key=b579c4a4933a4097a9a92709212412 &q={lat}, {lon}&aqi=no')
#     if response.status_code == 200:
#         response = response.json()
#         data = {
#             'name': response['location']['name'],
#             'region': response['location']['region'],
#             'country': response['location']['country'],
#             'lat': response['location']['lat'],
#             'lon': response['location']['lon'],
#             'temp_c': response['current']['temp_c'],
#             'temp_f': response['current']['temp_f']
#         }
#         all_responses.append(data)
#     else:
#         pass
# with open('all_weather_data.json', 'w') as f:
#     json.dump(all_responses, f)

"I ran this twice (once at 1030 am pst and once at 1030pm pst) to grab all the temperature data and compile into a json based on coordinates (lat, long). This takes about 5-6 hours to run."

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.colors import Normalize
from matplotlib.animation import FFMpegWriter
# %matplotlib qt

# def initialize_temperatures(H, average_temperatures):
#     average_temp = np.mean([temp[1] for temp in average_temperatures])
#     std = np.std([temp[1] for temp in average_temperatures])
#     return np.random.normal(average_temp, std, H.shape)

# def process_topography(H):
#     land_elevations = [elevation for elevation in H.flatten() if elevation > 0]
#     sea_elevations = [elevation for elevation in H.flatten() if elevation <= 0]
#     avg_land_elevation = round(np.average(land_elevations), 3)
#     avg_sea_elevation = round(np.average(sea_elevations), 3)
#     H_processed = np.where(H > 0, avg_land_elevation, avg_sea_elevation)
#     return H_processed

# def energy_balance_model_array(initial_temperatures, solar_radiation, albedo, emissivity=0.61, decades=1):
#     sigma = 5.67e-8  # stefan boltzmann constant in W/m^2K^4

#     initial_temps_k = (initial_temperatures - 32) * 5/9 + 273.15
#     equilibrium_temp_k = ((solar_radiation * (1 - albedo)) / (4 * sigma * emissivity)) ** 0.25
#     temp_changes_per_decade_k = equilibrium_temp_k - initial_temps_k
#     temp_changes_per_decade_f = temp_changes_per_decade_k * 9/5
#     max_temp_rise_per_decade_f = np.random.uniform(1.9, 2.1, size=initial_temperatures.shape)
#     temp_changes_per_decade_f = np.minimum(temp_changes_per_decade_f, max_temp_rise_per_decade_f)

#     final_temp_changes_k = temp_changes_per_decade_f * 5/9
#     final_temps_k = initial_temps_k + final_temp_changes_k * decades

#     final_temps_f = (final_temps_k - 273.15) * 9/5 + 32

#     return final_temps_f


def initialize_temperature_map(H, average_temperatures, data_am, data_pm):
    average_temp = np.mean([temp[1] for temp in average_temperatures])
    temp_range = np.arange(-89.2, 129.3, 0.1) 
    temp_lookup_am = {(entry['lat'], entry['lon']): entry['temp_f'] for entry in data_am}
    temp_lookup_pm = {(entry['lat'], entry['lon']): entry['temp_f'] for entry in data_pm}
    temperature_map = np.full(H.shape, 0.0) 
    total_cells = H.size
    filled_cells = 0
    cumulative_temp = 0
    
    for y in range(H.shape[0]):
        for x in range(H.shape[1]):
            lat, lon = get_coordinates(x, y)
            lat = round(lat, 2)
            lon = round(lon, 2)
            if (lat, lon) in temp_lookup_am and (lat, lon) in temp_lookup_pm:
                avg_temp = (temp_lookup_am[(lat, lon)] + temp_lookup_pm[(lat, lon)]) / 2
                temperature_map[y, x] = avg_temp
                cumulative_temp += avg_temp
                filled_cells += 1
            elif y > 150 and H[y][x] > 0:
                fraction = (y-150) / (180-150)
                avg_temp = fraction * np.random.uniform(-22.3,14.5)
                temperature_map[y,x] = avg_temp
                cumulative_temp += avg_temp
                filled_cells += 1
    remaining_cells = total_cells - filled_cells
    if remaining_cells > 0:
        remaining_average = (average_temp * total_cells - cumulative_temp) / remaining_cells
        closest_temp = min(temp_range, key=lambda x: abs(x - remaining_average))
        temperature_map[temperature_map == 0.0] = closest_temp

    return temperature_map

def load_and_shift_topography(filename):
    try:
        H = np.loadtxt(filename)
    except IOError:
        print("Error loading file")
        return None
    return np.roll(H, 180, axis=1)

def simulate_solar_radiation(H, temperature_map, dissipation_rate=0.001):
    absorbed_radiation = solar_radiation * (1 - albedo)
    heat_capacity_map = np.where(H <= 0, water_heat_capacity_F, soil_heat_capacity_F)
    temperature_change = absorbed_radiation * delta_t / heat_capacity_map
    if np.average(temperature_change) > 0:
        temperature_change = np.minimum(np.random.uniform(1.8,2.0, size=temperature_change.shape)/10, temperature_change)
    elif np.average(temperature_change) < 0:
            temperature_change = np.minimum(np.random.uniform(1.8,2.0, size=temperature_change.shape)/10, temperature_change)
    updated_temperature_map = temperature_map + temperature_change
    for i in range(H.shape[0]-1):
        for j in range(H.shape[1]-1):
            kappa = water_kappa if H[i][j] <= 0 else soil_kappa
            diffusion_term = (temperature_map[i+1][j] - 2 * temperature_map[i][j] + temperature_map[i-1][j]) / delta_x**2 + \
                             (temperature_map[i][j+1] - 2 * temperature_map[i][j] + temperature_map[i][j-1]) / delta_x**2
            diffusion_change = (kappa * diffusion_term * delta_t / heat_capacity_map[i][j])
            if diffusion_change > 0:
                updated_temperature_map[i][j] += min(np.random.uniform(1.8,2.0)/10, diffusion_change)
            elif diffusion_change < 0:
                updated_temperature_map[i][j] += max(np.random.uniform(-.8,-1.0)/10, diffusion_change)
    atmospheric_temperature = np.mean(updated_temperature_map)
    heat_dissipation = dissipation_rate * (updated_temperature_map - atmospheric_temperature) * delta_t
    heat_dissipation = np.where( heat_dissipation > 2, np.random.uniform(1.8, 2.0, size=heat_dissipation.shape) / 10,  heat_dissipation)
    heat_dissipation = np.where(heat_dissipation < -1, np.random.uniform(-0.8, -1.0, size=heat_dissipation.shape) / 10,  heat_dissipation)
    return updated_temperature_map

def solve_heat_equation_yearly_vectorized(temperature_grid, H_processed, elevation_diffusivity_factor=.0001):
    max_increase = np.random.uniform(1.9, 2.0) / 10
    solar_attenuation_factor = 0.00001
    new_temperature_grid = np.copy(temperature_grid)
    initial_temperature_grid = np.copy(temperature_grid)
    kappa_adjusted = np.where(H_processed > 0, soil_kappa * np.exp(-elevation_diffusivity_factor * H_processed), water_kappa)
    rho_C = np.where(H_processed > 0, soil_heat_capacity_F, water_heat_capacity_F)
    def periodic_roll(arr, shift, axis):
        return np.roll(arr, shift, axis=axis)
    diffusion_term = (periodic_roll(temperature_grid, -1, axis=0) - 2 * temperature_grid + periodic_roll(temperature_grid, 1, axis=0)) / delta_x**2 + \
                     (periodic_roll(temperature_grid, -1, axis=1) - 2 * temperature_grid + periodic_roll(temperature_grid, 1, axis=1)) / delta_x**2
    solar_effect = solar_radiation * (1 - albedo) * solar_attenuation_factor

    new_temperature_grid += kappa_adjusted * diffusion_term * delta_t / rho_C
    new_temperature_grid += solar_effect * delta_t / rho_C
    temperature_increase = new_temperature_grid - initial_temperature_grid
    excess_increase_mask = temperature_increase > max_increase
    new_temperature_grid[excess_increase_mask] = initial_temperature_grid[excess_increase_mask] + max_increase
    return new_temperature_grid


from matplotlib.colors import Normalize, LinearSegmentedColormap


def create_quadruple_colormap(cmap1, cmap2, cmap3, cmap4, temp_range, bin_thresholds):
    min_temp, max_temp = temp_range
    threshold_normalized1 = (bin_thresholds[0] - min_temp) / (max_temp - min_temp)
    threshold_normalized2 = (bin_thresholds[1] - min_temp) / (max_temp - min_temp)
    threshold_normalized3 = (bin_thresholds[2] - min_temp) / (max_temp - min_temp)

    colors1 = cmap1(np.linspace(0, 1, 256))[:int(256 * threshold_normalized1)]
    colors2 = cmap2(np.linspace(0, 1, 256))[int(256 * threshold_normalized1):int(256 * threshold_normalized2)]
    colors3 = cmap3(np.linspace(0, 1, 256))[int(256 * threshold_normalized2):int(256 * threshold_normalized3)]
    colors4 = cmap4(np.linspace(0, 1, 256))[int(256 * threshold_normalized3):]
    
    combined_colors = np.vstack((colors1, colors2, colors3, colors4))
    new_cmap = LinearSegmentedColormap.from_list('QuadrupleBlendedCmap', combined_colors)

    return new_cmap

def plot_topography_with_temperature(ax, H, temperature_grid, title, alpha, colorbar=None):
    ax.clear()
    ax.imshow(H, cmap='gray', interpolation='nearest')

    # Dynamic range based on temperature_grid
    min_temp = np.min(temperature_grid)
    max_temp = np.max(temperature_grid)
    norm = Normalize(vmin=min_temp, vmax=max_temp)

    # Define colormaps and transition temperatures
    cmap1 = plt.get_cmap('plasma')
    cmap2 = plt.get_cmap('winter')
    cmap3 = plt.get_cmap('autumn')
    cmap4 = plt.get_cmap('cool')
    
    bin_thresholds = (45, 130, 215) 

    # Create a custom blended colormap
    blended_cmap = create_quadruple_colormap(cmap1, cmap2, cmap3, cmap4, (min_temp, max_temp), bin_thresholds)

    temp_img = ax.imshow(temperature_grid, cmap=blended_cmap, interpolation='nearest', alpha=alpha, norm=norm)
    ax.set_title(title)

    # Update or create colorbar
    if colorbar:
        colorbar.update_normal(temp_img)
    else:
        colorbar = ax.figure.colorbar(temp_img, ax=ax, label='Temperature (°F)')

    # Set ticks for colorbar
#     step = 26
#     ticks = np.arange(min_temp, max_temp + step, step)
#     colorbar.set_ticks(ticks)

    return colorbar

    # Update the ticks for dynamic range
#     step = 26  # temperature step
#     ticks = np.arange(min_temp, max_temp + step, step)
#     colorbar.set_ticks(ticks)

#     # Set tick labels to match the ticks
#     tick_labels = [f"{t}°F" for t in ticks]
#     colorbar.set_ticklabels(tick_labels)

    return colorbar




average_temperatures = [
    (1875, 52.5),
    (1876, 51.5),
    (1877, 52.0),
    (1878, 52.5),
    (1879, 52.7),
    (1880, 48.6),
    (1881, 52.3),
    (1882, 49.6),
    (1883, 50.8),
    (1884, 51.0),
    (1885, 52.8),
    (1886, 52.0),
    (1887, 52.6),
    (1888, 53.0),
    (1889, 52.9),
    (1890, 51.4),
    (1891, 50.8),
    (1892, 51.2),
    (1893, 50.3),
    (1894, 51.0),
    (1895, 50.4),
    (1896, 51.6),
    (1897, 50.6),
    (1898, 49.7),
    (1899, 51.0),
    (1900, 53.9),
    (1901, 53.5),
    (1902, 52.1),
    (1903, 50.6),
    (1904, 51.8),
    (1905, 51.7),
    (1906, 51.2),
    (1907, 52.4),
    (1908, 50.1),
    (1909, 51.8),
    (1910, 54.5),
    (1911, 51.2),
    (1912, 50.9),
    (1913, 51.3),
    (1914, 53.2),
    (1915, 53.2),
    (1916, 51.1),
    (1917, 50.7),
    (1918, 52.3),
    (1919, 52.5),
    (1920, 51.3),
    (1921, 54.4),
    (1922, 51.2),
    (1923, 50.8),
    (1924, 51.5),
    (1925, 53.1),
    (1926, 53.9),
    (1927, 52.5),
    (1928, 50.7),
    (1929, 49.3),
    (1930, 49.4),
    (1931, 49.9),
    (1932, 48.2),
    (1933, 50.5),
    (1934, 55.3),
    (1935, 51.9),
    (1936, 52.2),
    (1937, 51.4),
    (1938, 52.0),
    (1939, 51.7),
    (1940, 53.8),
    (1941, 51.5),
    (1942, 49.7),
    (1943, 52.2),
    (1944, 49.4),
    (1945, 50.5),
    (1946, 52.0),
    (1947, 51.6),
    (1948, 50.6),
    (1949, 50.1),
    (1950, 51.6),
    (1951, 50.4),
    (1952, 51.1),
    (1953, 53.2),
    (1954, 52.8),
    (1955, 49.6),
    (1956, 51.5),
    (1957, 51.7),
    (1958, 53.6),
    (1959, 51.7),
    (1960, 51.9),
    (1961, 52.3),
    (1962, 50.6),
    (1963, 50.9),
    (1964, 48.3),
    (1965, 50.5),
    (1966, 52.4),
    (1967, 51.9),
    (1968, 50.3),
    (1969, 52.0),
    (1970, 51.6),
    (1971, 50.5),
    (1972, 52.3),
    (1973, 51.4),
    (1974, 52.9),
    (1975, 50.8),
    (1976, 51.6),
    (1977, 53.2),
    (1978, 53.3),
    (1979, 52.7),
    (1980, 52.8),
    (1981, 54.3),
    (1982, 51.0),
    (1983, 53.5),
    (1984, 51.0),
    (1985, 51.9),
    (1986, 52.7),
    (1987, 53.4),
    (1988, 53.3),
    (1989, 52.2),
    (1990, 53.4),
    (1991, 51.8),
    (1992, 53.6),
    (1993, 50.3),
    (1994, 54.7),
    (1995, 53.9),
    (1996, 54.3),
    (1997, 53.4),
    (1998, 52.9),
    (1999, 53.3),
    (2000, 53.7),
    (2001, 53.8),
    (2002, 52.0),
    (2003, 55.0),
    (2004, 52.1),
    (2005, 53.4),
    (2006, 53.8),
    (2007, 53.8),
    (2008, 51.9),
    (2009, 52.1),
    (2010, 52.7),
    (2011, 51.8),
    (2012, 56.6),
    (2013, 53.3),
    (2014, 55.6),
    (2015, 56.3),
    (2016, 56.2),
    (2017, 56.1),
    (2018, 56.2),
    (2019, 53.6),
    (2020, 55.7),
    (2021, 56.3),
    (2022, 55.9)
]

file_am = "all_weather_data_1030amPST.json"
file_pm = "all_weather_data_1030pmPST.json"
with open(file_am, 'r') as f_am, open(file_pm, 'r') as f_pm:
        data_am = json.load(f_am)
        data_pm = json.load(f_pm)

In [ ]:
# Main simulation parameters
num_runs = 100  # Number of Monte Carlo runs
simulation_years = 1000  # Number of years to simulate
delta_t = 24 * 60 * 60 * 365  # One year in seconds
solar_radiation = 340
soil_heat_capacity_C = 1500  # J/kg°C
water_heat_capacity_C = 4181  # J/kg°C
soil_heat_capacity_F = soil_heat_capacity_C / 1.8  # J/kg°F
water_heat_capacity_F = water_heat_capacity_C / 1.8  # J/kg°F
albedo = np.full(H.shape, 0.3)
delta_x = 111000
soil_kappa = 5*10e-7
water_kappa = 1.4*10e-7
H = load_and_shift_topography('topography_180x360_grid.txt')
# Initialize temperatures in (F)
temperatures = initialize_temperature_map(H, average_temperatures, data_am, data_pm)

def monte_carlo_simulation(H, num_runs):
    all_results = []
#     second_results = []
    initial_temps = []
    for run in range(num_runs):
        temperatures = initialize_temperature_map(H, average_temperatures, data_am, data_pm)
        initial_temps.append(temperatures)
    selected_run = np.random.choice(num_runs)
#     second_selected_run = np.random.choice(num_runs)
    first_frame_temp = simulate_solar_radiation(H, temperatures)
    colorbar = plot_topography_with_temperature(ax, H, first_frame_temp, f'Temperature Overlay Run {selected_run+1}, Year 1', alpha=0.8)
    with writer.saving(fig, "temperature_simulation_solar_radiation.mp4", 100):
        for year in range(simulation_years):
            temperatures = simulate_solar_radiation(H, temperatures)
            plot_topography_with_temperature(ax, H, temperatures, f'Temperature Overlay Run {selected_run+1}, Year {year+1}', alpha=0.8, colorbar=colorbar)
            writer.grab_frame()
            all_results.append(temperatures)
    return all_results

fig, ax = plt.subplots()
writer = FFMpegWriter(fps=15, metadata=dict(title='Temperature Simulation', artist='Matplotlib'))

mc_results = monte_carlo_simulation(H, num_runs)

In [ ]:
# Main simulation parameters
num_runs = 100  # Number of Monte Carlo runs
simulation_years = 1000  # Number of years to simulate
delta_t = 24 * 60 * 60 * 365  # One year in seconds
solar_radiation = 340
soil_heat_capacity_C = 1500  # J/kg°C
water_heat_capacity_C = 4181  # J/kg°C
soil_heat_capacity_F = soil_heat_capacity_C / 1.8  # J/kg°F
water_heat_capacity_F = water_heat_capacity_C / 1.8  # J/kg°F
albedo = np.full(H.shape, 0.3)
delta_x = 111000
soil_kappa = 5*10e-7
water_kappa = 1.4*10e-7
H = load_and_shift_topography('topography_180x360_grid.txt')
# Initialize temperatures in (F)
temperatures = initialize_temperature_map(H, average_temperatures, data_am, data_pm)

def monte_carlo_simulation(H, num_runs):
    all_results = []
#     second_results = []
    initial_temps = []
    for run in range(num_runs):
        temperatures = initialize_temperature_map(H, average_temperatures, data_am, data_pm)
        initial_temps.append(temperatures)
    selected_run = np.random.choice(num_runs)
#     second_selected_run = np.random.choice(num_runs)
    first_frame_temp = solve_heat_equation_yearly_vectorized(temperatures, H)
    colorbar = plot_topography_with_temperature(ax, H, first_frame_temp, f'Temperature Overlay Run {selected_run+1}, Year 1', alpha=0.8)
    with writer.saving(fig, "temperature_simulation_heat_equation.mp4", 100):
        for year in range(simulation_years):
            temperatures = solve_heat_equation_yearly_vectorized(temperatures, H)
            plot_topography_with_temperature(ax, H, temperatures, f'Temperature Overlay Run {selected_run+1}, Year {year+1}', alpha=0.8, colorbar=colorbar)
            writer.grab_frame()
            all_results.append(temperatures)
    return all_results

fig, ax = plt.subplots()
writer = FFMpegWriter(fps=15, metadata=dict(title='Temperature Simulation', artist='Matplotlib'))

mc2_results = monte_carlo_simulation(H, num_runs)

In [ ]:
def find_min_max(mc_results, iteration):
    biggest = -float("inf")
    smallest = float("inf")
    for i in range(len(mc_results[iteration])):
        for j in range(len(mc_results[iteration][1])):
            if biggest < mc_results[iteration][i][j]:
                biggest = max(biggest, mc_results[iteration][i][j])
            elif smallest > mc_results[iteration][i][j]:
                smallest = min(smallest, mc_results[iteration][i][j])
    print('Highest recorded temp', biggest)
    print('Lowest recorded temp', smallest)
    plt.figure(figsize=(10, 5))
    plt.imshow(H, cmap='gray', interpolation='nearest')
    norm = Normalize(vmin=np.min(mc_results[iteration]), vmax=np.max(mc_results[iteration]))
    plt.imshow(mc_results[0], cmap='plasma', interpolation='nearest', alpha=0.9, norm=norm)
    plt.colorbar(label='Temperature (°F)')
    plt.title(f'Results of iteration {iteration}')
    plt.show()
for i in range(0,1000,100):
    find_min_max(mc2_results, i)
for i in range(0,1000,100):
    find_min_max(mc_results, i)